# Review DPS outputs

Make a mosaic of DPS outputs.

1. make a list of the DPS output paths with build_tindex.master.py
2. Identify duplicate tiles
3. Identify matching tiles; merge tindex.master with the original index tile file
4. make mosaicjson
6. View DPS results

In [1]:
import geopandas
import pandas as pd
import os
import json
import collections

def local_to_s3(url, user = 'nathanmthomas', type='public'):
    ''' A Function to convert local paths to s3 urls'''
    if type is 'public':
        replacement_str = f's3://maap-ops-workspace/shared/{user}'
    else:
        replacement_str = f's3://maap-ops-workspace/{user}'
    return url.replace(f'/projects/my-{type}-bucket', replacement_str)

/projects/.local/lib/python3.7/site-packages/geopandas/_compat.py:110: UserWarning: The Shapely GEOS version (3.8.0-CAPI-1.13.1 ) is incompatible with the GEOS version PyGEOS was compiled with (3.9.1-CAPI-1.14.2). Conversions between both will be slow.
  shapely_geos_version, geos_capi_version_string


# Make a list of DPS outputs with build_tindex_master.py

In [2]:
DPS_DATA_TYPE = 'ATL08_filt' #"Topo" "Landsat" "ATL08" "ATL08_filt" "AGB"
DPS_DATA_USER = 'lduncanson' #'nathanmthomas'
tindex_master_fn = f'/projects/shared-buckets/{DPS_DATA_USER}/DPS_tile_lists/{DPS_DATA_TYPE}_tindex_master.csv'
ATL08_filt_sample_tindex_master_fn = f'/projects/shared-buckets/{DPS_DATA_USER}/DPS_tile_lists/ATL08_filt_sample_tindex_master.csv'
Topo_tindex_master_fn = f'/projects/shared-buckets/nathanmthomas/DPS_tile_lists/Topo_tindex_master.csv'

Topo_tindex_master =   pd.read_csv(Topo_tindex_master_fn)
atl08_filt_tindex_master =   pd.read_csv('s3://maap-ops-workspace/shared/lduncanson/DPS_tile_lists/ATL08_filt_tindex_master.csv')
ATL08_filt_sample_tindex_master = pd.read_csv(ATL08_filt_sample_tindex_master_fn)

UPDATE_TINDEX = False

if not os.path.isfile(tindex_master_fn):
    UPDATE_TINDEX = True
else:
    print('Using existing tindex')
    print(tindex_master_fn)
    
if UPDATE_TINDEX:
    print(f"Building master tile index for: {DPS_DATA_TYPE}")
    dps_month = 10
    os.system(f"python /projects/icesat2_boreal/lib/build_tindex_master.py --type {DPS_DATA_TYPE} -m {dps_month}")

Using existing tindex
/projects/shared-buckets/lduncanson/DPS_tile_lists/ATL08_filt_tindex_master.csv


In [3]:
# Build up a dataframe from the list of dps output files
tindex_master = pd.read_csv(tindex_master_fn)
tindex_master['s3'] = [local_to_s3(local_path, user='lduncanson', type = 'private') for local_path in tindex_master['local_path']]
print(len(tindex_master))

# Get all covar tiles that should account for the set of output we want
tiles_covars = pd.read_csv(Topo_tindex_master_fn).tile_num
print(len(tiles_covars))

# Get all boreal tiles
boreal_tile_index_path = '/projects/shared-buckets/nathanmthomas/boreal_grid_albers90k_gpkg.gpkg'
boreal_tile_index = geopandas.read_file(boreal_tile_index_path)
boreal_tile_index.astype({'layer':'int'})
boreal_tile_index.rename(columns={"layer":"tile_num"}, inplace=True)
boreal_tile_index["tile_num"] = boreal_tile_index["tile_num"].astype(int)

bad_tiles = [3540,3634,3728,3823,3916,4004] #Dropping the tiles near antimeridian that reproject poorly.

# For some reason, doing this causes 'MosaicJSON.from_features()' to fail...(below)
if True:
    # Remove bad tiles
    boreal_tile_index = boreal_tile_index[~boreal_tile_index['tile_num'].isin(bad_tiles)]
    
#print(boreal_tile_index.head())

3968
4433


# Identify duplicate tiles

In [4]:
duplicate_tiles = [item for item, count in collections.Counter(tindex_master["tile_num"]).items() if count > 1]
print(duplicate_tiles)

[986, 979, 980, 987, 981, 984, 982, 978, 985, 983, 988, 2203, 2296, 2298, 2355, 2357, 3540, 4004, 3728, 3634, 3916, 3823]


# Identify completed, missing, failed, & duplicate tiles

In [5]:
# Select the rows we have results for
tile_matches = boreal_tile_index.merge(tindex_master[~tindex_master['tile_num'].isin(bad_tiles)], how='right', on='tile_num')
tile_matches_atl08_filt_samples = boreal_tile_index.merge(ATL08_filt_sample_tindex_master[~ATL08_filt_sample_tindex_master['tile_num'].isin(bad_tiles)], how='right', on='tile_num')
print(f'Completed: \t\t{len(tile_matches)}')

import numpy as np
tile_nums_missing = np.setdiff1d(tiles_covars, tile_matches.tile_num)
#tile_index_missing = boreal_tile_index.merge(boreal_tile_index[boreal_tile_index['tile_num'].isin(tile_nums_missing)], how='right', on='tile_num')
tile_index_missing = boreal_tile_index.merge(Topo_tindex_master[Topo_tindex_master['tile_num'].isin(tile_nums_missing)], how='right', on='tile_num')
print(f'Missing (w/ dup ATL08 filt): \t\t{len(tile_index_missing)}')
tile_index_missing.to_csv(f'/projects/my-public-bucket/DPS_tile_lists/Need_{DPS_DATA_TYPE}_tindex_master.csv')
print(tile_index_missing.head())

tile_matches_failed = boreal_tile_index.merge(Topo_tindex_master[Topo_tindex_master['tile_num'].isin(tile_nums_missing)], how='right', on='tile_num')
print(f'Missing b/c failed: \t{len(tile_matches_failed)}')

tile_matches_duplicates = boreal_tile_index.merge(Topo_tindex_master[Topo_tindex_master['tile_num'].isin(duplicate_tiles)], how='right', on='tile_num')
print(f'Duplicates: \t\t{len(tile_matches_duplicates)}')

print(tile_matches.info())
tile_matches_geojson_string = tile_matches.to_crs("EPSG:4326").to_json()
tile_matches_geojson = json.loads(tile_matches_geojson_string)

tile_index_missing_geojson_string = tile_index_missing.to_crs("EPSG:4326").to_json()
tile_index_missing_geojson = json.loads(tile_index_missing_geojson_string)


Completed: 		3950
Missing (w/ dup ATL08 filt): 		499
   tile_num                                           geometry  Unnamed: 0  \
0       421  POLYGON ((4508522.000 7443304.000, 4598522.000...           0   
1       455  POLYGON ((4508522.000 7353304.000, 4598522.000...           1   
2       491  POLYGON ((4148522.000 7263304.000, 4238522.000...           3   
3       492  POLYGON ((4238522.000 7263304.000, 4328522.000...           4   
4       531  POLYGON ((4148522.000 7173304.000, 4238522.000...          10   

                                          local_path  
0  /projects/my-private-bucket/dps_output/do_topo...  
1  /projects/my-private-bucket/dps_output/do_topo...  
2  /projects/my-private-bucket/dps_output/do_topo...  
3  /projects/my-private-bucket/dps_output/do_topo...  
4  /projects/my-private-bucket/dps_output/do_topo...  
Missing b/c failed: 	499
Duplicates: 		22
<class 'geopandas.geodataframe.GeoDataFrame'>
Int64Index: 3950 entries, 0 to 3949
Data columns (total 6 co

## Build a MosaicJSON

In [6]:
from typing import Dict

from cogeo_mosaic.mosaic import MosaicJSON
from cogeo_mosaic.backends import MosaicBackend

def get_accessor(feature: Dict):
    """Return specific feature identifier."""
    return feature["properties"]["s3"]

In [7]:
out_mosaic_json_fn = f's3://maap-ops-workspace/shared/{DPS_DATA_USER}/DPS_tile_lists/{DPS_DATA_TYPE}_tindex_master_mosaic.json' 

mosaicdata = MosaicJSON.from_features(tile_matches_geojson.get('features'), minzoom=6, maxzoom=18, accessor=get_accessor)

with MosaicBackend(out_mosaic_json_fn, mosaic_def=mosaicdata) as mosaic:
    mosaic.write(overwrite=True)

/projects/.local/lib/python3.7/site-packages/mercantile/__init__.py:79: FutureWarning: Mercantile 2.0 will require tile x and y to be within the range (0, 2 ** zoom)
  FutureWarning,


## View the Results with Folium

In [8]:
from folium import Map, TileLayer, GeoJson, LayerControl, Icon, Marker, features, Figure, CircleMarker

In [ ]:
# Setup the mosaic tiling
tiler_base = "https://jqsd6bqdsf.execute-api.us-west-2.amazonaws.com/"
tiler_mosaic =  "".join([tiler_base, "mosaicjson/tiles/{z}/{x}/{y}"])

# Get a basemap
tiler_basemap_gray = "http://services.arcgisonline.com/ArcGIS/rest/services/Canvas/World_Light_Gray_Base/MapServer/tile/{z}/{y}/{x}"
tiler_basemap_image = 'https://services.arcgisonline.com/arcgis/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}'

# Get Vector layers
boreal_geojson = '/projects/shared-buckets/lduncanson/wwf_circumboreal_Dissolve.geojson'#'/projects/shared-buckets/nathanmthomas/boreal.geojson' 
boreal = geopandas.read_file(boreal_geojson)
ecoboreal_geojson = '/projects/shared-buckets/nathanmthomas/Ecoregions2017_boreal_m.geojson'
ecoboreal = geopandas.read_file(ecoboreal_geojson)

# Reproject Vector Layers
p1, p2, clat, clon = [50, 70, 40, 160]
proj_str_aea = '+proj=aea +lat_1={:.2f} +lat_2={:.2f} +lat_0={:.2f} +lon_0={:.2f}'.format(p1, p2, clat, clon)
ecoboreal_aea = ecoboreal.to_crs(proj_str_aea)
# Apply a buffer
ecoboreal_aea_buf = ecoboreal_aea["geometry"].buffer(1e5)
# Go back to GCS
ecoboreal_buf = ecoboreal_aea_buf.to_crs(boreal_tile_index.crs)

# Style Vector Layers
ecoboreal_style = {'fillColor': 'orange', 'color': 'orange'}
boreal_style = {'fillColor': 'gray', 'color': 'gray'}
boreal_subset_style = {'fillColor': 'red', 'color': 'red'}

# Map the Layers
Map_Figure=Figure(width=1500,height=800)
#------------------
m1 = Map(
    tiles="Stamen Toner",
    location=(60, 5),
    zoom_start=3
)
Map_Figure.add_child(m1)

#GeoJson(ecoboreal_aea_buf, name="Boreal extent from Ecoregions", style_function=lambda x:ecoboreal_style).add_to(m1)
GeoJson(boreal, name="Boreal extent", style_function=lambda x:boreal_style).add_to(m1)

boreal_tiles_style = {'fillColor': '#ff7f00', 'color': '#ff7f00'}
dps_subset_style = {'fillColor': '#377eb8', 'color': '#377eb8'}
dps_missing_style = {'fillColor': 'red', 'color': 'red'}

#GeoJson(atl08_gdf, name="ATL08"
#       ).add_to(m)

boreal_tile_index_layer = GeoJson(
        data=boreal_tile_index.to_crs("EPSG:4326").to_json(),
        style_function=lambda x:boreal_tiles_style,
        name="Boreal tiles",
        tooltip=features.GeoJsonTooltip(
            fields=['tile_num'],
            aliases=['Tile num:'],
        )
    )


tile_matches_layer = GeoJson(
        data=tile_matches_geojson,
        style_function=lambda x:dps_subset_style,
        name="AGB tiles: have",
        tooltip=features.GeoJsonTooltip(
            fields=['tile_num'],
            aliases=['Tile num:'],
        )
    )

if len(tile_index_missing) > 0:
    tile_matches_missing_layer = GeoJson(
            data=tile_index_missing_geojson,
            style_function=lambda x:dps_missing_style,
            name="AGB tiles: need"
        )
    

    
if True:
    basemaps = {
       'Google Terrain' : TileLayer(
        tiles = 'https://mt1.google.com/vt/lyrs=p&x={x}&y={y}&z={z}',
        attr = 'Google',
        name = 'Google Terrain',
        overlay = False,
        control = True
       ),
        'basemap_gray' : TileLayer(
            tiles=tiler_basemap_gray,
            opacity=1,
            name="World gray basemap",
            attr="MAAP",
            overlay=False
        ),
        'Imagery' : TileLayer(
            tiles=tiler_basemap_image,
            opacity=1,
            name="Imagery",
            attr="MAAP",
            overlay=False
        ),
        'landsat_tiles_layer' : TileLayer(
            tiles= f"{tiler_mosaic}?url=s3://maap-ops-workspace/shared/nathanmthomas/DPS_tile_lists/Landsat_mosaic.json&rescale=0.01,0.5&bidx=6&colormap_name=viridis",
            opacity=1,
            name="landsat covars",
            attr="MAAP",
            overlay=False
        ),
        'topo_tiles_layer' : TileLayer(
            tiles= f"{tiler_mosaic}?url=s3://maap-ops-workspace/shared/nathanmthomas/DPS_tile_lists/Topo_mosaic.json&rescale=0,1&bidx=3&colormap_name=bone",
            opacity=1,
            name="topo covars",
            attr="MAAP",
            overlay=False
        )#,
#         'hs_gee' : TileLayer(
#             tiles = 'https://earthengine.googleapis.com/v1alpha/projects/earthengine-legacy/maps/b38679fdddade79893d581fbcee738ed-89ea5f4b38d3c46a6a68d22113c50e7b/tiles/{z}/{x}/{y}',
#             opacity=1,
#             name="HS GEE",
#             attr="MAAP",
#             overlay=False
#         )
    }
    #agb_colormap = ['#636363','#fc8d59','#fee08b','#ffffbf','#d9ef8b','#91cf60','#1a9850']
    #agb_colormap={"1":"#5255A3", "2":"#1796A3", "3":"#FDBF6F", "4":"#FF7F00", "5":"#FFFFBF", "6":"#D9EF8B", "7":"#91CF60", "8":"#1A9850", "9":"#C4C4C4", "10":"#FF0000", "11":"#0000FF"}
    agb_colormap = 'viridis'#'RdYlGn_11' #'RdYlGn' #'nipy_spectral'
    # agb_colormap = cm.LinearColormap(colors=cm.linear.Spectral_11.colors, vmin=0, vmax=125)
    agb_tiles = f"{tiler_mosaic}?url=s3://maap-ops-workspace/shared/lduncanson/DPS_tile_lists/AGB_tindex_master_mosaic.json&rescale=0,125&bidx=1&colormap_name={agb_colormap}"
    agb_tiles_layer = TileLayer(
        tiles=agb_tiles,
        opacity=1,
        name="Boreal AGB",
        attr="MAAP",
        overlay=True
    )
    agb_se_colormap = 'magma'
    agb_se_tiles = f"{tiler_mosaic}?url=s3://maap-ops-workspace/shared/lduncanson/DPS_tile_lists/AGB_tindex_master_mosaic.json&rescale=0,20&bidx=2&colormap_name={agb_se_colormap}"
    agb_se_tiles_layer = TileLayer(
        tiles=agb_se_tiles,
        opacity=1,
        name="Boreal AGB SE",
        attr="MAAP",
        overlay=True
    )
    
    # Add custom basemaps
    basemaps['Google Terrain'].add_to(m1)
    basemaps['basemap_gray'].add_to(m1)
    basemaps['Imagery'].add_to(m1)
    #basemaps['hs_gee'].add_to(m1)
    if False:
        basemaps['landsat_tiles_layer'].add_to(m1)
        basemaps['topo_tiles_layer'].add_to(m1)
    
    agb_tiles_layer.add_to(m1)
    agb_se_tiles_layer.add_to(m1)
    
    # Layers are added on top. Last layer is top layer
    boreal_tile_index_layer.add_to(m1)
    tile_matches_layer.add_to(m1)
    tile_matches_missing_layer.add_to(m1)
    #tile_matches_n_obs.add_to(m1)    
    
LayerControl().add_to(m1)

import branca.colormap as cm
colormap_AGB = cm.linear.viridis.scale(0, 125).to_step(25)
colormap_AGB.caption = 'Mean of Aboveground Biomass Density [Mg/ha]'
#colormap_AGBSE = cm.linear.magma.scale(0, 20).to_step(5)
#colormap_AGBSE.caption = 'Standard Error of Aboveground Biomass Density [Mg/ha]'

m1.add_child(colormap_AGB)
#m1.add_child(colormap_AGBSE)

m1

In [2]:
import branca.colormap as cm

pal_height_cmap = cm.LinearColormap(colors = ['black','#636363','#fc8d59','#fee08b','#ffffbf','#d9ef8b','#91cf60','#1a9850'], vmin=0, vmax=10)
pal_height_cmap.caption = 'Vegetation height from  ATL08 @ 30 m (h_can; rh98)'
pal_height_cmap
#colormap = cm.linear.nipy_spectral.scale(0, 125).to_step(25)
#colormap

In [3]:
# import matplotlib.pyplot as plt
# import matplotlib
# print(matplotlib.__version__)
# cmap = plt.cm.get_cmap('Spectral')
# cmap
# plt.cm.datad.keys()

nobs_cmap = cm.LinearColormap(colors=cm.linear.RdYlGn_11.colors, vmin=0, vmax=15000)
nobs_cmap
nobs_cmap_samples_night = cm.LinearColormap(colors=cm.linear.viridis.colors, vmin=0, vmax=250)
nobs_cmap_samples_night

tile_num                                           geometry  Unnamed: 0  \
0       986  POLYGON ((4598522.000 6273304.000, 4688522.000...           0   
1       979  POLYGON ((3968522.000 6273304.000, 4058522.000...           1   
2       980  POLYGON ((4058522.000 6273304.000, 4148522.000...           2   
3       987  POLYGON ((4688522.000 6273304.000, 4778522.000...           3   
4       981  POLYGON ((4148522.000 6273304.000, 4238522.000...           4   

                                          local_path    n_obs  \
0  /projects/my-private-bucket/dps_output/run_til...  12272.0   
1  /projects/my-private-bucket/dps_output/run_til...   3759.0   
2  /projects/my-private-bucket/dps_output/run_til...   5409.0   
3  /projects/my-private-bucket/dps_output/run_til...   7746.0   
4  /projects/my-private-bucket/dps_output/run_til...  10113.0   

                                                  s3      color  
0  s3://maap-ops-workspace/lduncanson/dps_output/...  #58b75fff  
1  s3://maap-ops-workspace/lduncanson/dps_output/...  #f98e52ff  
2  s3://maap-ops-workspace/lduncanson/dps_output/...  #fecd7aff  
3  s3://maap-ops-workspace/lduncanson/dps_output/...  #f9fdb7ff  
4  s3://maap-ops-workspace/lduncanson/dps_output/...  #b3df72ff

In [17]:
def map_tile_n_obs(tindex_master_fn='s3://maap-ops-workspace/shared/lduncanson/DPS_tile_lists/ATL08_filt_tindex_master.csv', 
                   max_n_obs=15000, color_pal_name='RdYlGn_11', map_width=1000, map_height=200, 
                   boreal_tile_index_path = '/projects/shared-buckets/nathanmthomas/boreal_grid_albers90k_gpkg.gpkg'):
    
    import pandas as pd
    import geopandas
    import branca.colormap as cm
    
    # Build up a dataframe from the list of dps output files
    tindex_master = pd.read_csv(tindex_master_fn)
   

    # Get all boreal tiles
    boreal_tile_index = geopandas.read_file(boreal_tile_index_path)
    #boreal_tile_index.astype({'layer':'int'})
    boreal_tile_index.rename(columns={"layer":"tile_num"}, inplace=True)
    boreal_tile_index["tile_num"] = boreal_tile_index["tile_num"].astype(int)

    bad_tiles = [3540,3634,3728,3823,3916,4004] #Dropping the tiles near antimeridian that reproject poorly.

    boreal_tile_index = boreal_tile_index[~boreal_tile_index['tile_num'].isin(bad_tiles)]
    tile_matches = boreal_tile_index.merge(tindex_master[~tindex_master['tile_num'].isin(bad_tiles)], how='right', on='tile_num')
    
    nobs_cmap = cm.LinearColormap(colors=cm.linear.RdYlGn_11.colors, vmin=0, vmax=15000)

    tile_matches['color'] = [nobs_cmap(n_obs) for n_obs in tile_matches.n_obs]


    Map_Figure3=Figure(width=map_width,height=map_height)
    
    m3 = Map(
        tiles="Stamen Toner",
        location=(60, 5),
        zoom_start=2
    )
    Map_Figure3.add_child(m3)

    tile_matches_n_obs = GeoJson(
        tile_matches,
        style_function=lambda feature: {
            'fillColor': feature['properties']['color'],
            #'color' : feature['properties']['color'],
            'color' : 'black',
            'weight' : 1,
            'fillOpacity' : 0.5,
            },
        name="ATL08 filt tiles: n_obs",
        tooltip=features.GeoJsonTooltip(
                fields=['n_obs'],
                aliases=['# obs.:'],
            )
        )
    tile_matches_n_obs.add_to(m3)
    colormap_nobs= nobs_cmap.scale(0, 15000).to_step(15)
    colormap_nobs.caption = '# of obs'
    m3.add_child(colormap_nobs)

    if False:
        tile_matches_atl08_filt_samples_n_obs = GeoJson(
            tile_matches_atl08_filt_samples,
            style_function=lambda feature: {
                'fillColor': feature['properties']['color'],
                #'color' : feature['properties']['color'],
                'color' : 'black',
                'weight' : 1,
                'fillOpacity' : 0.5,
                },
            name="ATL08 filt sample tiles: n_obs",
            tooltip=features.GeoJsonTooltip(
                    fields=['n_obs'],
                    aliases=['# obs.:'],
                )
            )

        tile_matches_atl08_filt_samples_n_obs.add_to(m3)
        nobs_cmap_samples_night.scale(0, 250).to_step(15)
        nobs_cmap_samples_night.caption = '# of SAMPLE obs'
        m3.add_child(nobs_cmap_samples_night)

    LayerControl().add_to(m3)

    return m3